In [1]:
%load_ext autoreload
%autoreload 2

import logging
from dotenv import load_dotenv

logging.basicConfig(level=logging.INFO)
load_dotenv()

True

In [2]:
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
import numpy as np
import logging
import pandas as pd

from typing import Optional
from pydantic import BaseModel


logger = logging.getLogger(__name__)

class RegressionModelEvalOutput(BaseModel):
    """
    Definitions:
        - rmse: Root Mean Squared Error
            - Range: [0, ∞)
            - Lower is better
            - Penalizes large errors more than small ones (sensitive to outliers)
            - Good when large mistakes are especially costly

        - mae: Mean Absolute Error
            - Range: [0, ∞)
            - Lower is better
            - Treats all errors equally (linear penalty)
            - More robust to outliers than RMSE

        - mape: Mean Absolute Percentage Error
            - Range: [0, ∞)
            - Lower is better
            - Expresses error as a percentage of actual values
            - Can be misleading when actual values are near zero

        - r2: R-squared (Coefficient of Determination)
            - Range: (-∞, 1]
            - Higher is better
            - Measures proportion of variance in the target explained by the model
            - Negative values mean the model is worse than predicting the mean
    """
    rmse: float
    mae: float
    mape: float
    r2: float

class RegressionModelEvalOverfittingAnalysis(BaseModel):
    rmse_degradation: float
    r2_degradation: float

class RegressionTestTrainModelEvalOutput(BaseModel):
    train_metrics: RegressionModelEvalOutput
    test_metrics: RegressionModelEvalOutput
    overfitting_analysis: RegressionModelEvalOverfittingAnalysis

# MARK: - Model Evaluation
def evaluate_model(y_true: pd.Series, y_pred: pd.Series):
    """Calculate the metrics for actual vs predicted"""
    
    mse = mean_squared_error(y_true, y_pred)
    rmse = np.sqrt(mse)
    mae = mean_absolute_error(y_true, y_pred)
    r2 = r2_score(y_true, y_pred)
    
    # Calculate MAPE (Mean Absolute Percentage Error)
    # Avoid division by zero and handle edge case of all zeros
    mask = y_true != 0
    if np.sum(mask) > 0:
        mape = np.mean(np.abs((y_true[mask] - y_pred[mask]) / y_true[mask])) * 100
    else:
        mape = np.nan  # All true values are zero
    
    return RegressionModelEvalOutput(
        rmse=rmse,
        mae=mae,
        mape=float(mape),
        r2=float(r2)
    )
    
def evaluate_test_train_models(
    y_train: pd.Series,
    y_train_pred: pd.Series,
    y_test: pd.Series,
    y_test_pred: pd.Series,
):
    
    train_metrics = evaluate_model(y_train, y_train_pred)
    test_metrics = evaluate_model(y_test, y_test_pred)

    return RegressionTestTrainModelEvalOutput(
        train_metrics=train_metrics,
        test_metrics=test_metrics,
        overfitting_analysis=RegressionModelEvalOverfittingAnalysis(
            rmse_degradation=(test_metrics.rmse - train_metrics.rmse) / train_metrics.rmse * 100,
            r2_degradation=(train_metrics.r2 - test_metrics.r2) / train_metrics.r2 * 100,
        )
    )

In [3]:
from xgboost import XGBRegressor
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import OneHotEncoder, StandardScaler, PolynomialFeatures, OrdinalEncoder
from sklearn.compose import ColumnTransformer
from sklearn.feature_selection import SelectKBest, f_regression
from sklearn.impute import SimpleImputer
from typing import Any
import logging
import numpy as np

logger = logging.getLogger(__name__)


def get_pipeline(
    ohe_cols: list[str],
    num_cols: list[str],
    boolean_cols: list[str],
    top_n_features: int | None = None,
    max_categories: int = 30,
    xgboost_params: dict[str, Any] | None = None,
):
    """
    Create a machine learning pipeline with preprocessing and XGBoost.
    
    Args:
        ohe_cols: Columns to apply one-hot encoding
        num_cols: Numerical columns to scale and apply polynomial features
        boolean_cols: Boolean columns to convert to integers
        top_n_features: Number of top features to select (None for no feature selection)
        max_categories: Maximum categories for one-hot encoding (None for no limit)
        missing_value_threshold: Columns with missing values above this threshold (0-1) will be dropped
        xgboost_params: XGBoost parameters (None for default parameters)
        
    Returns:
        Configured sklearn Pipeline
    """    
    preprocessor = ColumnTransformer(
        transformers=[
            ('num', Pipeline([
                ('imputer', SimpleImputer(strategy='constant', fill_value=0)),
                ('scaler', StandardScaler()),
                ('poly', PolynomialFeatures(degree=2, include_bias=False))
            ]), num_cols),
            ('cat', Pipeline([
                ('imputer', SimpleImputer(strategy='constant', fill_value='unknown')),
                ('onehot', OneHotEncoder(
                        handle_unknown='ignore', 
                        sparse_output=False,
                        max_categories=max_categories
                    )
                )
            ]), ohe_cols),
            ('bool', Pipeline([
                ('encoder', OrdinalEncoder()),
                ('imputer', SimpleImputer(strategy='constant', fill_value=-1)),
            ]), boolean_cols),
        ],
        remainder='drop',
    )

    preprocessor.set_output(transform="pandas")

    if xgboost_params is None:
        xgboost_params = {
            'n_estimators': 1000,  # Set high, early stopping will control
            'learning_rate': 0.05,  # Reduced from 0.1
            'max_depth': 3,  # Reduced from 5
            'min_child_weight': 5,  # Added regularization
            'subsample': 0.7,  # Added subsampling
            'colsample_bytree': 0.8,  # Added feature subsampling
            'reg_alpha': 1.0,  # L1 regularization
            'reg_lambda': 5.0,  # L2 regularization
            'gamma': 0.1,  # Minimum loss reduction for split
            'random_state': 42,
            'n_jobs': -1
        }
    # XGBoost pipeline
    steps = [
        ('preprocessor', preprocessor),
    ]
    if top_n_features is not None:
        steps.append(('feature_selection', SelectKBest(f_regression, k=top_n_features))) # type: ignore
        
    steps.append(('xgboost', XGBRegressor(**xgboost_params)))

    pipeline = Pipeline(steps)

    logger.info(f'Pipeline created for {ohe_cols} + {num_cols} + {boolean_cols}')
    return pipeline

In [5]:
from projects.pltv.session import get_session
from projects.pltv.feature_store import get_dataset

session = get_session()
sp_df = get_dataset(session, '80242617')

INFO:src.connection:Creating session from private key
INFO:snowflake.connector.connection:Snowflake Connector for Python Version: 3.18.0, Python Version: 3.10.18, Platform: macOS-26.1-arm64-arm-64bit
INFO:snowflake.connector.connection:Connecting to GLOBAL Snowflake domain
INFO:snowflake.snowpark.session:Snowpark Session information: 
"version" : 1.42.0,
"python.version" : 3.10.18,
"python.connector.version" : 3.18.0,
"python.connector.session.id" : 23301350163286,
"os.name" : Darwin

INFO:root:Using database ML_LAYER
INFO:root:Creating schema PLTV
INFO:root:Using schema PLTV
INFO:src.connection:Reinstating connections from active session
INFO:snowflake.ml.feature_store.feature_store:Successfully connected to feature store: ML_LAYER.PLTV_FS.
INFO:src.services.feature_store_service:Spine PLTV SPINE created
/Users/donatodiferdinando/Documents/GitHub/ml-layer-v2/.venv/lib/python3.10/site-packages/snowflake/ml/feature_store/feature_store.py:189: UserWarning: Entity PLTV_ENTITY already exis

In [6]:
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

df = sp_df.to_pandas()
# df.to_parquet('dataset.parquet')
# df = pd.read_parquet('dataset.parquet').sample(1000000)
print(len(df))


1734


In [7]:
df.sort_values(by='DATE_DAY', inplace=True)
df

DATE_DAY  CUSTOMER_ID  GROSS_ADD_ID  SUB_TREE_ID SUB_TREE_TYPE  \
533   2021-02-26    152650364      78555863     80242617         cross   
1678  2021-02-27    152650364      78555863     80242617         cross   
145   2021-02-28    152650364      78555863     80242617         cross   
103   2021-03-01    152650364      78555863     80242617         cross   
1189  2021-03-02    152650364      78555863     80242617         cross   
1554  2021-03-03    152650364      78555863     80242617         cross   
490   2021-03-04    152650364      78555863     80242617         cross   
62    2021-03-05    152650364      78555863     80242617         cross   
1556  2021-03-06    152650364      78555863     80242617         cross   
1636  2021-03-07    152650364      78555863     80242617         cross   
411   2021-03-08    152650364      78555863     80242617         cross   
1106  2021-03-09    152650364      78555863     80242617         cross   
1063  2021-03-10    152650364      78555863     80242617         cross   
532   2021-03-11    152650364      78555863     80242617         cross   
143   2021-03-12    152650364      78555863     80242617         cross   
105   2021-03-13    152650364      78555863     80242617         cross   
572   2021-03-14    152650364      78555863     80242617         cross   
107   2021-03-15    152650364      78555863     80242617         cross   
491   2021-03-16    152650364      78555863     80242617         cross   
1512  2021-03-17    152650364      78555863     80242617         cross   
1022  2021-03-18    152650364      78555863     80242617         cross   
108   2021-03-19    152650364      78555863     80242617         cross   
371   2021-03-20    152650364      78555863     80242617         cross   
1145  2021-03-21    152650364      78555863     80242617         cross   
1635  2021-03-22    152650364      78555863     80242617         cross   
1147  2021-03-23    152650364      78555863     80242617         cross   
493   2021-03-24    152650364      78555863     80242617         cross   
1435  2021-03-25    152650364      78555863     80242617         cross   
1065  2021-03-26    152650364      78555863     80242617         cross   
1515  2021-03-27    152650364      78555863     80242617         cross   
1144  2021-03-28    152650364      78555863     80242617         cross   
1104  2021-03-29    152650364      78555863     80242617         cross   
109   2021-03-30    152650364      78555863     80242617         cross   
144   2021-03-31    152650364      78555863     80242617         cross   
185   2021-04-01    152650364      78555863     80242617         cross   
1148  2021-04-02    152650364      78555863     80242617         cross   
1105  2021-04-03    152650364      78555863     80242617         cross   
249   2021-04-04    152650364      78555863     80242617         cross   
1066  2021-04-05    152650364      78555863     80242617         cross   
1064  2021-04-06    152650364      78555863     80242617         cross   
410   2021-04-07    152650364      78555863     80242617         cross   
1433  2021-04-08    152650364      78555863     80242617         cross   
982   2021-04-09    152650364      78555863     80242617         cross   
980   2021-04-10    152650364      78555863     80242617         cross   
1185  2021-04-11    152650364      78555863     80242617         cross   
537   2021-04-12    152650364      78555863     80242617         cross   
102   2021-04-13    152650364      78555863     80242617         cross   
574   2021-04-14    152650364      78555863     80242617         cross   
450   2021-04-15    152650364      78555863     80242617         cross   
370   2021-04-16    152650364      78555863     80242617         cross   
652   2021-04-17    152650364      78555863     80242617         cross   
1676  2021-04-18    152650364      78555863     80242617         cross   
1594  2021-04-19    152650364      78555863     80242617         cross   
495   2021-0

In [ ]:
TARGET_COL = 'NET_BILLINGS_NEXT_730_DAYS'
# TARGET_COLS: list[str] = [
    # 'NET_BILLINGS_NEXT_30_DAYS',
    # 'NET_BILLINGS_NEXT_60_DAYS',
    # 'NET_BILLINGS_NEXT_90_DAYS',
    # 'NET_BILLINGS_NEXT_180_DAYS',
    # 'NET_BILLINGS_NEXT_365_DAYS',
    # 'NET_BILLINGS_NEXT_730_DAYS',
    # 'NET_BILLINGS_NEXT_1095_DAYS',
# ]

PASS_THROUGH_COLS: list[str] = [
    'DATE_DAY',
    'CUSTOMER_ID',
    'GROSS_ADD_ID',
    'SUB_TREE_ID',
]

cat_cols: list[str] = [
    'SUB_TREE_TYPE', 
    'BRAND_SLUG', 
    'SKU_TYPE_SLUG', 
    'CHANNEL_SLUG', 
    'TRAFFIC_SOURCE_SHORT_NAME',  
    'PLAN_SKU', 
    'PLAN_RECURRING_INTERVAL', 
    'STATUS', 
    'ORDER_PLAN_SKU', 
    'ORDER_RECURRING_INTERVAL', 
    'PAYMENT_PROCESSOR_GROUP_NAME', 
    'BIN', 
    'PAYMENT_OPTION_PAYMENT_TYPE', 
    'PAYMENT_OPTION_CARD_NETWORK', 
    'PAYMENT_OPTION_EXP_DATE', 
    'PAYMENT_OPTION_STATE', 
    'PAYMENT_OPTION_ZIP', 
    'PAYMENT_OPTION_CITY',
    # high null columns
    'CAMPAIGN_ID',
    'PLAN_PROMO_INTERVAL',
    'LAST_FAILURE_CODE',
    'LAST_FAILURE_MESSAGE',
    'MERCHANT_ACCOUNT_ID',
    'ORDER_PROMO_INTERVAL',
]
num_cols: list[str] = [
    'CYCLE',
    'PLAN_RECURRING_PERIOD', 
    'PLAN_RECURRING_PRICE', 
    'DAYS_SINCE_START_OF_TIME', 
    'DAYS_SINCE_CUSTOMER_CREATED', 
    'DAYS_SINCE_GROSS_ADD_CREATED', 
    'DAYS_SINCE_LAST_SUCCESSFUL_INITIAL_PAYMENT', 
    'NET_BILLINGS_TO_DATE', 
    'ORDER_RECURRING_PERIOD', 
    'ORDER_RECURRING_PRICE', 
    'DAYS_SINCE_PLAN_REPLACEMENT', 
    'DAYS_SINCE_PAYMENT_OPTION_REPLACEMENT',
    # high null columns
    'PLAN_PROMO_PERIOD',
    'PLAN_PROMO_PRICE',
    'PLAN_PROMO_PRICE_SPREAD',
    'FAILED_REBILLS',
    'DAYS_SINCE_LAST_SUCCESSFUL_RRCBT',
    'ORDER_PROMO_PERIOD', 
    'ORDER_PROMO_PRICE', 
    'ORDER_PROMO_PRICE_SPREAD'
]

bool_cols: list[str] = [
    'IS_CANCELED',
]

stratify_cols = ['BRAND_SLUG']

In [ ]:
df[df['SUB_TREE_ID'] == 80242617]

In [ ]:
X = df
X

In [ ]:
y = df[TARGET_COL].fillna(0)
y

In [ ]:
from sklearn.model_selection import train_test_split

kwargs = {
    "test_size": 0.2,
    "random_state": 42,
}
if len(stratify_cols) > 0:
    kwargs["stratify"] = X[stratify_cols]
X_train, X_test, y_train, y_test = train_test_split(
    X, 
    y, 
    **kwargs
)

In [ ]:
pipeline = get_pipeline(
    ohe_cols=cat_cols,
    num_cols=num_cols,
    boolean_cols=[],
)

In [ ]:
pipeline.fit(X_train, y_train)

In [ ]:
y_train_pred = pipeline.predict(X_train)
y_test_pred = pipeline.predict(X_test)

In [ ]:
evaluate_test_train_models(
    y_train=y_train,
    y_train_pred=y_train_pred,
    y_test=y_test,
    y_test_pred=y_test_pred,
).model_dump()

In [ ]:
df_test = X_test.copy()
df_test['y_true'] = y_test
df_test['y_pred'] = y_test_pred
df_test.head(50)
